In [11]:
from sklearn import metrics
import pickle
import scipy
from matplotlib import pyplot as plt
from sklearn.datasets import make_checkerboard
from sklearn.cluster.bicluster import SpectralBiclustering
import numpy as np
import json as simplejson

In [8]:
matrix = pickle.load(open("s5d2np_numpy.dump","rb"))

lngth = 30000
last_ind = (len(matrix[0])/lngth)+1
cos_matrix = [[[0 for i in range(113)]for j in range(61)]for k in range(61)]
matrix = scipy.stats.zscore(np.array(matrix))

In [23]:
fin_matrix = [[0 for i in range(last_ind)] for j in range(1891)]

In [ ]:
for i in range(61):
    for j in range(61):
        for intervals in range(last_ind):
            if intervals == last_ind-1:
                cos_matrix[i][j][last_ind-1] = metrics.pairwise.cosine_similarity(matrix[i][last_ind-1 * lngth:], 
                                                                                  matrix[j][last_ind-1*lngth:])
            else:
                cos_matrix[i][j][intervals] = metrics.pairwise.cosine_similarity(matrix[i][intervals * lngth:(intervals + 1) * lngth],
                                                                                 matrix[j][intervals * lngth:(intervals + 1) * lngth])

C:\Users\Paul\Anaconda2\lib\site-packages\sklearn\utils\validation.py:386: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and willraise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  DeprecationWarning)
C:\Users\Paul\Anaconda2\lib\site-packages\sklearn\utils\validation.py:386: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and willraise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  DeprecationWarning)
C:\Users\Paul\Anaconda2\lib\site-packages\sklearn\utils\validation.py:386: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and willraise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  DeprecationWarning)
C

In [24]:
# converts node vs node to edges vs time
cntr = 0
for i in range(61):
    for j in range(61):
        if i >= j:
            for n in range(last_ind):
                fin_matrix[cntr][n] = cos_matrix[i][j][n]
            cntr += 1
            
for i in range(len(fin_matrix)):
    for j in range(len(fin_matrix[0])):
        fin_matrix[i][j] = fin_matrix[i][j][0][0]

In [3]:
print fin_matrix

[[0.99999964, 0.99999958, 0.99999988, 1.0, 1.0, 1.0000004, 1.0, 0.99999976, 1.0000001, 1.0000005, 0.99999988, 1.0, 1.0000001, 0.9999997, 1.0000001, 0.99999976, 1.0, 1.0, 1.0, 1.0, 0.99999994, 1.0000001, 0.9999997, 1.0, 0.99999994, 0.99999976, 0.99999976, 1.0, 1.0, 0.99999964, 1.0000002, 0.99999964, 1.0000001, 1.0000002, 1.0000002, 0.99999982, 0.99999964, 1.0, 1.0, 0.99999994, 0.9999997, 0.99999952, 0.99999946, 1.0, 0.99999988, 1.0, 1.0, 0.99999994, 1.0000005, 0.99999988, 1.0000002, 0.99999994, 0.99999982, 0.99999976, 1.0, 0.9999997, 1.0000001, 0.99999946, 1.0, 1.0000002, 1.0000002, 1.0000001, 0.99999958, 1.0000005, 0.99999964, 0.99999988, 0.99999988, 0.99999964, 1.0000005, 1.0000002, 1.0000002, 0.99999988, 1.0000002, 1.0000002, 1.0, 0.99999952, 1.0, 1.0000001, 1.0000001, 0.99999976, 0.99999976, 1.0000002, 1.0000002, 0.9999997, 1.0, 0.9999997, 1.0000001, 1.0000002, 1.0000001, 0.99999994, 1.0000001, 0.99999976, 1.0, 0.99999994, 1.0000001, 0.99999946, 0.9999997, 1.0000006, 0.99999964, 1.0

In [4]:
# pickle.dump(fin_matrix, open("fin_matrix.dump", "wb"))
fin_matrix = pickle.load(open("fin_matrix.dump", "rb"))

plt.matshow(fin_matrix, cmap=plt.cm.Blues,aspect='auto')
plt.title("Cosine Similarity")
plt.show()

In [18]:
post_process_data = np.array(fin_matrix)
spectral_model = SpectralBiclustering()
spectral_model.fit(post_process_data)
fit_data = post_process_data[np.argsort(spectral_model.row_labels_)]
fit_data = fit_data[:, np.argsort(spectral_model.column_labels_)]
plt.matshow(post_process_data, cmap=plt.cm.Blues)
plt.title('Original Cos after Band and Z-Score 30s intervals\n')
plt.show()
plt.matshow(fit_data, cmap=plt.cm.Blues)
plt.title('Biclustered Cos after Band and Z-Score 30s intervals\n')
plt.show()

with open('z-score-cos-matrix-30s.json', 'w+') as f:
    p = [[float(column) for column in row] for row in fin_matrix]
    f.write(simplejson.dumps({'name': 's5d2nap', 'data': p}))

cols = np.argsort(spectral_model.column_labels_)
rows = np.argsort(spectral_model.row_labels_)
with open('fitted-indices-z-score-cos-30s_float.json', 'w+') as f:
    p = [[float(column) for column in cols] for row in rows]
    f.write(simplejson.dumps({'name': 's5d2nap', 'data': p}))

# with open('cos_sim.json', 'w') as f:
#      json.dump(np.array(json.loads(json.dumps(json_matrix.tolist))),f)

In [17]:
print len(fin_matrix), len(fin_matrix[0])

1891 113
